In [1]:
# Code to accompany the paper "Constructions in combinatorics via neural networks and LP solvers" by A Z Wagner
# Code for conjecture 2.1, without the use of numba 
#
# Please keep in mind that I am far from being an expert in reinforcement learning. 
# If you know what you are doing, you might be better off writing your own code.
#
# This code works on tensorflow version 1.14.0 and python version 3.6.3
# It mysteriously breaks on other versions of python.
# For later versions of tensorflow there seems to be a massive overhead in the predict function for some reason, and/or it produces mysterious errors.
# Debugging these was way above my skill level.
# If the code doesn't work, make sure you are using these versions of tf and python.
# I used keras version 2.3.1, not sure if this is important, but I recommend this just to be safe.

import networkx as nx #for various graph parameters, such as eigenvalues, macthing number, etc
import random
import numpy as np
import copy
import keras
from keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import SGD, Adam
from keras.models import load_model
from statistics import mean
from math import sqrt
from numpy.random import choice
import pickle
import time
import math
import matplotlib.pyplot as plt

In [2]:
from stabilizer_search.search.brute_force import *
from stabilizer_search.mat import X, T
from stabilizer_search.mat import tensor
from Gen_stab_partial import get_stabilizer_states as py_get_stabs

In [5]:
n_qubits = 4
chi = 4

In [6]:
extra = np.zeros((1, pow(2, n_qubits), 1)) #all-0s vector

In [7]:
# plus = np.array([[1/sqrt(2)], [1/sqrt(2)]], dtype=np.complex_)
# H = T*plus
H = [[np.cos(np.pi/8)],[np.sin(np.pi/8)]]
target_state = tensor(*([H]*n_qubits))
real = np.allclose(np.imag(target_state), 0.)
real

True

In [8]:
stabilizer_states = py_get_stabs(n_qubits, real_only=False)
n_stab_states = len(stabilizer_states)
n_stab_states

13856

In [9]:
stabilizers = [stabilizer_states[i] for i in range(n_stab_states) if np.allclose(stabilizer_states[i].imag, extra[0])]
n_stabilizers = len(stabilizers)
n_stabilizers

1568

In [10]:
#Add the all 0s vector as an option in case fewer entries suffice to get the decomposition
stabilizers = np.append(stabilizers, extra, 0)
#shuffle(stabilizers)

In [11]:
# Daochen: would be easier if could enforce the use of combinations
# MYN = int(2**n)  #The length of the word we are generating. Here we are generating a Boolean function on n bits, so we create a 0-1 word of length 2^n

MYN = int(chi)

# LEARNING_RATE = 0.0001 #Increase this to make convergence faster, decrease if the algorithm gets stuck in local optima too often.
LEARNING_RATE = 0.00001
n_sessions = 1000 #number of new sessions per iteration
# default 93, 94 respectively
percentile = 93 #top 100-X percentiled we are learning from
super_percentile = 96 #top 100-X percentile that survives to next iteration

# These are hyperparameters
FIRST_LAYER_NEURONS = 128 #Number of neurons in the hidden layers.
SECOND_LAYER_NEURONS = 64
THIRD_LAYER_NEURONS = 4

# n_actions = 2
# Daochen: note that this parameter is not actually used anywhere.
n_actions = n_stabilizers+1
#The size of the alphabet. In this file we will assume this is 2. There are a few things we need to change when the alphabet size is larger,
#such as one-hot encoding the input, and using categorical_crossentropy as a loss function.

observation_space = 2*MYN 

# Leave this at 2*MYN. The input vector will have size 2*MYN, 
# where the first MYN letters encode our partial word (with zeros on
# the positions we haven't considered yet), and the next MYN bits one-hot encode which letter we are considering now.
# So e.g. [0,1,0,0,   0,0,1,0] means we have the partial word 01 and we are considering the third letter now.
# Is there a better way to format the input to make it easier for the neural network to understand things?

# Daochen: why should len_game have anything to do with MYN
len_game = MYN 
state_dim = (observation_space,)

INF = 1000000

#Model structure: a sequential network with three hidden layers, sigmoid activation in the output.
#I usually used relu activation in the hidden layers but play around to see what activation function and what optimizer works best.
#It is important that the loss is binary cross-entropy if alphabet size is 2.

model = Sequential()
model.add(Dense(FIRST_LAYER_NEURONS,  activation="relu"))
model.add(Dense(SECOND_LAYER_NEURONS, activation="relu"))
model.add(Dense(THIRD_LAYER_NEURONS, activation="relu"))
model.add(Dense(n_actions, activation="softmax"))
model.build((None, observation_space))
model.compile(loss="sparse_categorical_crossentropy", optimizer=Adam(learning_rate = LEARNING_RATE)) #Adam optimizer also works well, with lower learning rate

print(model.summary())

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense (Dense)                (None, 128)               1152      
_________________________________________________________________
dense_1 (Dense)              (None, 64)                8256      
_________________________________________________________________
dense_2 (Dense)              (None, 4)                 260       
_________________________________________________________________
dense_3 (Dense)              (None, 1569)              7845      
Total params: 17,513
Trainable params: 17,513
Non-trainable params: 0
_________________________________________________________________
None


In [12]:
def calcScore(state):
    """
    Calculates the reward for a given word. 
    This function is very slow, it can be massively sped up with numba -- but numba doesn't support networkx yet, which is very convenient to use here
    :param state: the first MYN letters of this param are the word that the neural network has constructed.

    :returns: the reward (a real number). Higher is better, the network will try to maximize this.
    """

    sol = state[:MYN];
    candidate_stabilizer_basis = [stabilizers[sol[i]] for i in range(MYN) if not np.array_equal(stabilizers[sol[i]], extra[0])] #Ignore the all-0 string for the basis
    projector = ortho_projector(candidate_stabilizer_basis)
    projection = np.linalg.norm(projector*target_state, 2)
#     projection = 1
    
    score = projection
    target = score
    
    if np.allclose(score, 1):
        print('You found a stabilizer decomposition with (n_qubits,chi) = ', [n_qubits,chi])
        print('The set of stabilizers is: ', f)
    return target, score

####No need to change anything below here. 
# Daochen: the agent argument will be the "model"
def generate_session(agent, n_sessions, verbose = 1):
    """
    Play n_session games using agent neural network.
    Terminate when games finish 

    Code inspired by https://github.com/yandexdataschool/Practical_RL/blob/master/week01_intro/deep_crossentropy_method.ipynb
    """
    states =  np.zeros([n_sessions, observation_space, len_game], dtype=int)
    actions = np.zeros([n_sessions, len_game], dtype = int)
    state_next = np.zeros([n_sessions,observation_space], dtype = int)
    prob = np.zeros(n_sessions)
    states[:,MYN,0] = 1
    step = 0
    total_target = np.zeros([n_sessions])
#     total_target = np.zeros([n_sessions], dtype=complex)
    total_score = np.zeros([n_sessions])
    recordsess_time = 0
    play_time = 0
    scorecalc_time = 0
    pred_time = 0
    while (True):
        step += 1
        tic = time.time()
        prob = agent.predict(states[:,:,step-1], batch_size = n_sessions) 
        pred_time += time.time()-tic

        for i in range(n_sessions):
            action = choice(n_actions, p=prob[i])
#             print('probability vector: ', prob[i],' and action chosen: ', action)
            
#             if np.random.rand() < prob[i]:
#                 action = 1
#             else:
#                 action = 0
            actions[i][step-1] = action
            tic = time.time()
            state_next[i] = states[i,:,step-1]
            play_time += time.time()-tic
            if (action > 0):
                state_next[i][step-1] = action
            state_next[i][MYN + step-1] = 0
            if (step < MYN):
                state_next[i][MYN + step] = 1
#                 Daochen: terminal equals whether step equals MYN: I suppose meaning that an entire state has been generated
            terminal = step == MYN
            tic = time.time()
            if terminal:
#                 print('state_next[i]', state_next[i])
                total_target[i], total_score[i] = calcScore(state_next[i])
#                 print("total_score", total_score[i])
            scorecalc_time += time.time()-tic
            tic = time.time()
            if not terminal:
                states[i,:,step] = state_next[i]
            recordsess_time += time.time()-tic
        if terminal:
            break
    #If you want, print out how much time each step has taken. This is useful to find the bottleneck in the program.		
    if (verbose):
        print("Predict: "+str(pred_time)+", play: " + str(play_time) +", scorecalc: " + str(scorecalc_time) +", recordsess: " + str(recordsess_time))
        with open('Run'+str(myRand)+'.txt', 'a') as f:
            f.write("Predict: "+str(pred_time)+", play: " + str(play_time) +", scorecalc: " + str(scorecalc_time) +", recordsess: " + str(recordsess_time))
    return states, actions, total_score, total_target

def select_elites(states_batch, actions_batch, rewards_batch, percentile=50):
    """
    Select states and actions from games that have rewards >= percentile
    :param states_batch: list of lists of states, states_batch[session_i][t]
    :param actions_batch: list of lists of actions, actions_batch[session_i][t]
    :param rewards_batch: list of rewards, rewards_batch[session_i]

    :returns: elite_states,elite_actions, both 1D lists of states and respective actions from elite sessions

    This function was mostly taken from https://github.com/yandexdataschool/Practical_RL/blob/master/week01_intro/deep_crossentropy_method.ipynb
    If this function is the bottleneck, it can easily be sped up using numba
    """
    counter = n_sessions * (100.0 - percentile) / 100.0
    reward_threshold = np.percentile(rewards_batch,percentile)

    elite_states = []
    elite_actions = []
    elite_rewards = []
    for i in range(len(states_batch)):
        if rewards_batch[i] >= reward_threshold-0.0000001:
            if (counter > 0) or (rewards_batch[i] >= reward_threshold+0.0000001):
                for item in states_batch[i]:
                    elite_states.append(item.tolist())
                for item in actions_batch[i]:
                    elite_actions.append(item)
            counter -= 1
    elite_states = np.array(elite_states, dtype = int)
    elite_actions = np.array(elite_actions, dtype = int)
    return elite_states, elite_actions

def select_super_sessions(states_batch, actions_batch, rewards_batch, targets_batch, percentile=90):
    """
    Select all the sessions that will survive to the next generation
    Similar to select_elites function
    If this function is the bottleneck, it can easily be sped up using numba
    """
    counter = n_sessions * (100.0 - percentile) / 100.0
    reward_threshold = np.percentile(rewards_batch,percentile)

    super_states = []
    super_actions = []
    super_rewards = []
    super_targets = []
    for i in range(len(states_batch)):
        if rewards_batch[i] >= reward_threshold-0.0000001:
            if (counter > 0) or (rewards_batch[i] >= reward_threshold+0.0000001):
                super_states.append(states_batch[i])
                super_actions.append(actions_batch[i])
                super_rewards.append(rewards_batch[i])
                super_targets.append(targets_batch[i])
                counter -= 1
    super_states = np.array(super_states, dtype = int)
    super_actions = np.array(super_actions, dtype = int)
    super_rewards = np.array(super_rewards)
    super_targets = np.array(super_targets)
    return super_states, super_actions, super_rewards, super_targets

In [13]:
super_states =  np.empty((0,len_game,observation_space), dtype = int)
super_actions = np.array([], dtype = int)
super_rewards = np.array([])
super_targets= np.array([])
sessgen_time = 0
fit_time = 0
score_time = 0

myRand = random.randint(0,1000) #used in the filename
index = 0 #used to index generation

In [14]:
for i in range(5000): #1000000 generations should be plenty
    #generate new sessions
    #performance can be improved with joblib
    tic = time.time()
#     sessions = states, actions, total_score, total_target
    sessions = generate_session(model,n_sessions,0) #change 0 to 1 to print out how much time each step in generate_session takes 
    sessgen_time = time.time()-tic
    tic = time.time()

    states_batch = np.array(sessions[0], dtype = int)
    actions_batch = np.array(sessions[1], dtype = int)
    rewards_batch = np.array(sessions[2])
    targets_batch = np.array(sessions[3])
    
    states_batch = np.transpose(states_batch,axes=[0,2,1])
    states_batch = np.append(states_batch,super_states,axis=0)

    if i>0:
        actions_batch = np.append(actions_batch,np.array(super_actions),axis=0)	
    
    rewards_batch = np.append(rewards_batch,super_rewards)
    targets_batch = np.append(targets_batch,super_targets)

    randomcomp_time = time.time()-tic 
    tic = time.time()

    elite_states, elite_actions = select_elites(states_batch, actions_batch, rewards_batch, percentile=percentile) #pick the sessions to learn from
    select1_time = time.time()-tic

    tic = time.time()
    super_sessions = select_super_sessions(states_batch, actions_batch, rewards_batch, targets_batch, percentile=super_percentile) #pick the sessions to survive
    select2_time = time.time()-tic

    tic = time.time()
    super_sessions = [(super_sessions[0][i], super_sessions[1][i], super_sessions[2][i], super_sessions[3][i]) for i in range(len(super_sessions[2]))]
    super_sessions.sort(key=lambda super_sessions: super_sessions[2],reverse=True)
    select3_time = time.time()-tic

    tic = time.time()
    model.fit(elite_states, elite_actions) #learn from the elite sessions
    fit_time = time.time()-tic

    tic = time.time()

    super_states = [super_sessions[i][0] for i in range(len(super_sessions))]
    super_actions = [super_sessions[i][1] for i in range(len(super_sessions))]
    super_rewards = [super_sessions[i][2] for i in range(len(super_sessions))]
    super_targets = [super_sessions[i][3] for i in range(len(super_sessions))]
    
#     print(super_states)

    rewards_batch.sort()
#     Daochen: why is it -100?
    mean_all_reward = np.mean(rewards_batch[-100:])
    mean_best_reward = np.mean(super_rewards)

    score_time = time.time()-tic

    print("\n" + str(i) +  ". Best individuals (reward): " + str(np.flip(np.sort(super_rewards))))
#     Daochen: note that sometimes it makes sense to add/remove np.flip below
    print("\n" + str(i) +  ". Best individuals (target): " + str(np.flip(np.sort(super_targets))))

    #uncomment below line to print out how much time each step in this loop takes. 
    print("Mean reward: " + str(mean_all_reward) + "\nSessgen: " + str(sessgen_time) + ", other: " + str(randomcomp_time) + ", select1: " + str(select1_time) + ", select2: " + str(select2_time) + ", select3: " + str(select3_time) +  ", fit: " + str(fit_time) + ", score: " + str(score_time))
    
    with open('Run'+str(myRand)+'.txt', 'a') as f:
        f.write("\n" + str(i) +  ". Best individuals (reward): " + str(np.flip(np.sort(super_rewards))))
        f.write("\n" + str(i) +  ". Best individuals (target): " + str(np.sort(super_targets)))
        f.write("Mean reward: " + str(mean_all_reward) + "\nSessgen: " + str(sessgen_time) + ", other: " + str(randomcomp_time) + ", select1: " + str(select1_time) + ", select2: " + str(select2_time) + ", select3: " + str(select3_time) +  ", fit: " + str(fit_time) + ", score: " + str(score_time)+"\n")

    if (i%20 == 1): #Write all important info to files every 20 iterations
#         with open('best_species_pickle_'+str(myRand)+'.txt', 'wb') as fp:
#             pickle.dump(super_actions, fp)
        with open('super_actions_'+str(myRand)+'.txt', 'a') as f:
            f.write("At i = "+str(i)+":"+"\n")
            for item in super_actions:
                f.write(str(item))
                f.write("\n")
        with open('super_rewards_'+str(myRand)+'.txt', 'a') as f:
            f.write("At i = "+str(i)+":"+"\n")
            for item in super_rewards:
                f.write(str(item))
                f.write("\n")
        with open('mean_rewards_'+str(myRand)+'.txt', 'a') as f:
             f.write("At i = "+str(i)+": "+ str(mean_all_reward)+"\n")
        with open('mean_best_rewards_'+str(myRand)+'.txt', 'a') as f:
             f.write("At i = "+str(i)+": "+ str(mean_best_reward)+"\n")
                
#     if (i%25 == 1): #Write all important info to files every 20 iterations
#         with open('best_species_pickle_'+str(myRand)+'.txt', 'wb') as fp:
#             pickle.dump(super_actions, fp)
#         with open('best_species_txt_'+str(myRand)+'.txt', 'w') as f:
#             for item in super_actions:
#                 f.write(str(item))
#                 f.write("\n")
#         with open('best_species_rewards_'+str(myRand)+'.txt', 'w') as f:
#             for item in super_rewards:
#                 f.write(str(item))
#                 f.write("\n")
#         with open('best_100_rewards_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(mean_all_reward)+"\n")
#         with open('best_elite_rewards_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(mean_best_reward)+"\n")
#     if (i%200==2): # To create a timeline, like in Figure 3
#         with open('best_species_timeline_txt_'+str(myRand)+'.txt', 'a') as f:
#             f.write(str(super_actions[0]))
#             f.write("\n")

9/9 [==============================] - 0s 2ms/step - loss: 6.7762

0. Best individuals (reward): [0.87870887 0.85638157 0.84910003 0.84801683 0.84024502 0.82003968
 0.80925672 0.80843625 0.80760192 0.79956785 0.79902897 0.7953293
 0.79353927 0.79185993 0.79168945 0.77777779 0.77765569 0.77720268
 0.77621407 0.77619747 0.77534226 0.77414994 0.77374511 0.77363748
 0.76926912 0.7674223  0.76055879 0.75393383 0.75318298 0.75317744]

0. Best individuals (target): [0.87870887 0.85638157 0.84910003 0.84801683 0.84024502 0.82003968
 0.80925672 0.80843625 0.80760192 0.79956785 0.79902897 0.7953293
 0.79353927 0.79185993 0.79168945 0.77777779 0.77765569 0.77720268
 0.77621407 0.77619747 0.77534226 0.77414994 0.77374511 0.77363748
 0.76926912 0.7674223  0.76055879 0.75393383 0.75318298 0.75317744]
Mean reward: 0.7364217452917997
Sessgen: 2.105536460876465, other: 0.0, select1: 0.0009980201721191406, select2: 0.0009999275207519531, select3: 0.0, fit: 0.43197083473205566, score: 0.00101828575134277

10/10 [==============================] - 0s 2ms/step - loss: 6.7219

9. Best individuals (reward): [0.89580134 0.89004374 0.88367105 0.87899228 0.87870887 0.87064502
 0.86945003 0.86876255 0.86844988 0.866624   0.86623998 0.86341006
 0.85858783 0.85731405 0.85638157 0.85412542 0.85351622 0.85348584
 0.85250764 0.85130711 0.85056133 0.85051004 0.85036045 0.85014871
 0.84915524 0.84910003 0.84801683 0.84710363 0.84647111 0.84645949
 0.84509065]

9. Best individuals (target): [0.89580134 0.89004374 0.88367105 0.87899228 0.87870887 0.87064502
 0.86945003 0.86876255 0.86844988 0.866624   0.86623998 0.86341006
 0.85858783 0.85731405 0.85638157 0.85412542 0.85351622 0.85348584
 0.85250764 0.85130711 0.85056133 0.85051004 0.85036045 0.85014871
 0.84915524 0.84910003 0.84801683 0.84710363 0.84647111 0.84645949
 0.84509065]
Mean reward: 0.7899933930462686
Sessgen: 1.7523856163024902, other: 0.0, select1: 0.00099945068359375, select2: 0.0009999275207519531, select3: 0.0, fit: 0.06328225135803223,

10/10 [==============================] - 0s 2ms/step - loss: 6.6641

18. Best individuals (reward): [0.93683919 0.93646162 0.89580134 0.89375009 0.89004374 0.88367105
 0.88249572 0.87899334 0.87899228 0.87870887 0.87575596 0.87533105
 0.8746541  0.87166702 0.87064502 0.86945003 0.86906425 0.86876255
 0.86844988 0.86705057 0.866624   0.86623998 0.86567126 0.86398458
 0.86341006 0.85858783 0.85772809 0.85741026 0.85731405 0.85638157
 0.85412542]

18. Best individuals (target): [0.93683919 0.93646162 0.89580134 0.89375009 0.89004374 0.88367105
 0.88249572 0.87899334 0.87899228 0.87870887 0.87575596 0.87533105
 0.8746541  0.87166702 0.87064502 0.86945003 0.86906425 0.86876255
 0.86844988 0.86705057 0.866624   0.86623998 0.86567126 0.86398458
 0.86341006 0.85858783 0.85772809 0.85741026 0.85731405 0.85638157
 0.85412542]
Mean reward: 0.7903220519849335
Sessgen: 2.537165403366089, other: 0.0, select1: 0.0010001659393310547, select2: 0.00099945068359375, select3: 0.0, fit: 0.07499313354492188

10/10 [==============================] - 0s 2ms/step - loss: 6.5134

26. Best individuals (reward): [0.93683919 0.93646162 0.90709215 0.90446964 0.89580134 0.89375009
 0.89004374 0.886011   0.88367105 0.88249572 0.88166959 0.88058412
 0.88014263 0.87899334 0.87899228 0.87870887 0.87862494 0.87829991
 0.87575596 0.87533105 0.8746541  0.87405832 0.87166702 0.8715981
 0.87064502 0.87021842 0.86945003 0.86906425 0.86876255 0.86844988
 0.86796963]

26. Best individuals (target): [0.93683919 0.93646162 0.90709215 0.90446964 0.89580134 0.89375009
 0.89004374 0.886011   0.88367105 0.88249572 0.88166959 0.88058412
 0.88014263 0.87899334 0.87899228 0.87870887 0.87862494 0.87829991
 0.87575596 0.87533105 0.8746541  0.87405832 0.87166702 0.8715981
 0.87064502 0.87021842 0.86945003 0.86906425 0.86876255 0.86844988
 0.86796963]
Mean reward: 0.798531414197265
Sessgen: 2.3936986923217773, other: 0.0, select1: 0.002008676528930664, select2: 0.0, select3: 0.0, fit: 0.06178617477416992, score: 0.0
10/10 

10/10 [==============================] - 0s 2ms/step - loss: 6.4420

35. Best individuals (reward): [0.93683919 0.93646162 0.90709215 0.90446964 0.89580134 0.89375009
 0.89004374 0.88943988 0.88702206 0.886011   0.88367105 0.88353649
 0.88249572 0.88166959 0.88058412 0.88014263 0.87899334 0.87899228
 0.87870887 0.87862494 0.87829991 0.87575596 0.87550521 0.87533105
 0.87524688 0.8746541  0.87456196 0.87422708 0.87405832 0.8733215
 0.87328517]

35. Best individuals (target): [0.93683919 0.93646162 0.90709215 0.90446964 0.89580134 0.89375009
 0.89004374 0.88943988 0.88702206 0.886011   0.88367105 0.88353649
 0.88249572 0.88166959 0.88058412 0.88014263 0.87899334 0.87899228
 0.87870887 0.87862494 0.87829991 0.87575596 0.87550521 0.87533105
 0.87524688 0.8746541  0.87456196 0.87422708 0.87405832 0.8733215
 0.87328517]
Mean reward: 0.8087665167846521
Sessgen: 2.86629581451416, other: 0.0, select1: 0.0019979476928710938, select2: 0.001001119613647461, select3: 0.0, fit: 0.07699990272521973, 

...

9/9 [==============================] - 0s 2ms/step - loss: 0.0016

4961. Best individuals (reward): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]

4961. Best individuals (target): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]
Mean reward: 0.9878626242638364
Sessgen: 1.922398567199707, other: 0.0, select1: 0.0019578933715820312, select2: 0.0010042190551757812, select3: 0.0, fit: 0.06399869918823242, score: 0.0
9/9 [==

9/9 [==============================] - 0s 2ms/step - loss: 0.0017

4970. Best individuals (reward): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]

4970. Best individuals (target): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]
Mean reward: 0.9878626242638364
Sessgen: 1.9304475784301758, other: 0.0, select1: 0.001998424530029297, select2: 0.0, select3: 0.0, fit: 0.06408286094665527, score: 0.0
9/9 [====================

9/9 [==============================] - 0s 2ms/step - loss: 0.0016

4979. Best individuals (reward): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]

4979. Best individuals (target): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]
Mean reward: 0.9878626242638364
Sessgen: 1.9535934925079346, other: 0.0, select1: 0.0019981861114501953, select2: 0.0010013580322265625, select3: 0.0, fit: 0.07099366188049316, score: 0.0
9/9 [=

9/9 [==============================] - 0s 2ms/step - loss: 0.0016

4988. Best individuals (reward): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]

4988. Best individuals (target): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]
Mean reward: 0.9878626242638364
Sessgen: 1.9099934101104736, other: 0.0, select1: 0.0020072460174560547, select2: 0.00099945068359375, select3: 0.0, fit: 0.06195640563964844, score: 0.0
9/9 [===

9/9 [==============================] - 0s 2ms/step - loss: 0.0196

4997. Best individuals (reward): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]

4997. Best individuals (target): [0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262
 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262 0.98786262]
Mean reward: 0.9878626242638364
Sessgen: 1.9249536991119385, other: 0.0, select1: 0.0019996166229248047, select2: 0.0009999275207519531, select3: 0.0, fit: 0.06599926948547363, score: 0.0
9/9 [=

In [ ]:
state =  [294, 1419, 1535, 93, 1281, 1328]

In [ ]:
state[1]

In [ ]:
solution = [stabilizers[state[k]].real for k in range(len(state))]

In [ ]:
solution